In [2]:
try:
    import elasticsearch
    from elasticsearch import Elasticsearch
    
    import pandas as pd
    import json
    from ast import literal_eval
    from tqdm import tqdm
    import datetime
    import os
    import sys
    
    import os
    import numpy as np
    
    from elasticsearch import helpers
    print("Loaded  .. . . . . . . .")
except Exception as E:
    print("Some Modules are Missing {} ".format(E))

Loaded  .. . . . . . . .


In [3]:
df = pd.read_excel("elastic_Search_Data.xlsx")
print("read")

read


In [4]:
df.head()

filename country           Product name  \
0  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
1  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
2  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
3  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
4  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   

              Refined Product Name  \
0  Atacand (Candesartan Cilexetil)   
1  Atacand (Candesartan Cilexetil)   
2  Atacand (Candesartan Cilexetil)   
3  Atacand (Candesartan Cilexetil)   
4  Atacand (Candesartan Cilexetil)   

                                           para_text  \
0  ATACAND (candesartan cilexetil) is indicated f...   
1  Geriatrics (> 65 years of age) : No overall di...   
2  Pediatrics (6 to 17 years of age): \n•\tHypert...   
3  ATACAND (candesartan cilexetil) is contraindic...   
4  There is evidence that co-administration of an...   

                                  Possible Questions  Comment  
0  What is ATACAND used for\nWhat is ATACAND used...      NaN  
1  What is the efficacy of ATACAND in elderly pop...      NaN  
2  What is ATACAND used for in children\nWhat is ...      NaN  
3  Who is ATACAND conracindicated in\nWho is ATAC...      NaN  
4  Can ATACAND be co-administered with aliskiren\...      NaN

In [5]:
from bert_serving.client import BertClient
bc = BertClient()

In [6]:
answers=list(df["para_text"])

In [7]:
answers

['ATACAND (candesartan cilexetil) is indicated for: \n\n•\tHypertension\no\tThe treatment of mild to moderate essential hypertension.\no\tATACAND may be used alone or concomitantly with thiazide diuretics.\no\tThe safety and efficacy of concurrent use with calcium channel blockers have not been established.\n•\tHeart Failure\no\tThe treatment of NYHA Class II and III heart failure with ejection fraction\n≤ 40% in addition to standard therapy, with or without an ACE inhibitor. ',
 'Geriatrics (> 65 years of age) : No overall differences in safety or effectiveness were observed between these subjects and younger subjects, and other reported clinical experience has not identified differences in responses between the elderly and younger patients, but greater sensitivity of some older individuals cannot be ruled out. ',
 'Pediatrics (6 to 17 years of age): \n•\tHypertension\nATACAND is indicated for the treatment of essential hypertension in children and adolescents 6 to 17 years of age (se

In [8]:
bert_vec=bc.encode(answers)

In [63]:
type(bert_vec)

numpy.ndarray

In [21]:
bio_vec=[]
for x in bert_vec:
    bio_vec.append(x)

In [23]:
len(bio_vec)

99

In [24]:
df["bert_vec"]=bio_vec

In [64]:
type(df["bert_vec"])

pandas.core.series.Series

In [65]:
df["bert_vec"].to_pickle("./bio_bert_series.pkl")

In [66]:
os.getcwd()

'/home/srinivas/Downloads'

In [25]:
df.head()

filename country           Product name  \
0  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
1  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
2  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
3  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   
4  Candesartan_PM_Reviewed.docx  Canada  Candesartan cilexetil   

              Refined Product Name  \
0  Atacand (Candesartan Cilexetil)   
1  Atacand (Candesartan Cilexetil)   
2  Atacand (Candesartan Cilexetil)   
3  Atacand (Candesartan Cilexetil)   
4  Atacand (Candesartan Cilexetil)   

                                           para_text  \
0  ATACAND (candesartan cilexetil) is indicated f...   
1  Geriatrics (> 65 years of age) : No overall di...   
2  Pediatrics (6 to 17 years of age): \n•\tHypert...   
3  ATACAND (candesartan cilexetil) is contraindic...   
4  There is evidence that co-administration of an...   

                                  Possible Questions  Comment  \
0  What is ATACAND used for\nWhat is ATACAND used...      NaN   
1  What is the efficacy of ATACAND in elderly pop...      NaN   
2  What is ATACAND used for in children\nWhat is ...      NaN   
3  Who is ATACAND conracindicated in\nWho is ATAC...      NaN   
4  Can ATACAND be co-administered with aliskiren\...      NaN   

                                            bert_vec  
0  [-0.21258338, -0.09253818, -0.07741149, 0.2087...  
1  [-0.17276935, -0.36519173, -0.11895171, 0.1485...  
2  [-0.27216527, -0.07298208, -0.04816349, 0.1704...  
3  [-0.07860148, -0.18961588, -0.08207953, 0.0538...  
4  [-0.21261308, 0.14762478, -0.07835619, -0.0553...

In [9]:
type(bert_vec[0])

numpy.ndarray

In [26]:
len(bert_vec[0])

768

In [27]:
Settings = {
   "settings":{
      "number_of_shards":1,
      "number_of_replicas":0
   },
   "mappings":{
       "dynamic": "true",
        "_source": {
        "enabled": "true"
        },
       "properties":{
            "answer": {
            "type": "text"
            },
          "bert_vector":{
         "type":"dense_vector",
         "dims":768
      },   
          "country":{  
            "type":"keyword"
         },   
          "product":{  
            "type":"keyword"
         }
      

    }
   }
}

In [28]:
ENDPOINT = "http://localhost:9200/"
es = Elasticsearch(timeout=600,hosts=ENDPOINT)
print("python client created")

python client created


In [29]:
#creating the database
IndexName = 'bert_vec'
my = es.indices.create(index=IndexName, ignore=[400,404], body=Settings)

In [30]:
my

{'error': {'root_cause': [{'type': 'resource_already_exists_exception',
    'reason': 'index [bert_vec/Mk3nV8MNQqqmP4AmN1vMpw] already exists',
    'index_uuid': 'Mk3nV8MNQqqmP4AmN1vMpw',
    'index': 'bert_vec'}],
  'type': 'resource_already_exists_exception',
  'reason': 'index [bert_vec/Mk3nV8MNQqqmP4AmN1vMpw] already exists',
  'index_uuid': 'Mk3nV8MNQqqmP4AmN1vMpw',
  'index': 'bert_vec'},
 'status': 400}

In [31]:
df.columns

Index(['filename', 'country', 'Product name', 'Refined Product Name',
       'para_text', 'Possible Questions', 'Comment', 'bert_vec'],
      dtype='object')

In [32]:
df22 = df.to_dict('records')
df22

[{'filename': 'Candesartan_PM_Reviewed.docx',
  'country': 'Canada',
  'Product name': 'Candesartan cilexetil',
  'Refined Product Name': 'Atacand (Candesartan Cilexetil)',
  'para_text': 'ATACAND (candesartan cilexetil) is indicated for: \n\n•\tHypertension\no\tThe treatment of mild to moderate essential hypertension.\no\tATACAND may be used alone or concomitantly with thiazide diuretics.\no\tThe safety and efficacy of concurrent use with calcium channel blockers have not been established.\n•\tHeart Failure\no\tThe treatment of NYHA Class II and III heart failure with ejection fraction\n≤ 40% in addition to standard therapy, with or without an ACE inhibitor. ',
  'Possible Questions': 'What is ATACAND used for\nWhat is ATACAND used for in Canada\nHow can ATACAND be used\nHow can ATACAND be used in Canada\nCan ATACAND be used with calcium channel blockers\nCan ATACAND be used with calcium channel blockers in Canada\nCan ATACAND (candesartan cilexetil) be indicated for heartfailure',
  

In [33]:
len(df22)

99

In [34]:
arr=[]
for c, line in enumerate(df22):
    arr.append({"answer":line.get("para_text",""),
    'bert_vector':line.get("bert_vec",""),
    'country':line.get("country","").lower().strip(),
    'product':line.get("Product name","").lower().strip()})

In [35]:
arr

[{'answer': 'ATACAND (candesartan cilexetil) is indicated for: \n\n•\tHypertension\no\tThe treatment of mild to moderate essential hypertension.\no\tATACAND may be used alone or concomitantly with thiazide diuretics.\no\tThe safety and efficacy of concurrent use with calcium channel blockers have not been established.\n•\tHeart Failure\no\tThe treatment of NYHA Class II and III heart failure with ejection fraction\n≤ 40% in addition to standard therapy, with or without an ACE inhibitor. ',
  'bert_vector': array([-2.12583378e-01, -9.25381780e-02, -7.74114877e-02,  2.08734050e-01,
          2.33869419e-01, -1.54881567e-01, -1.55370012e-01, -2.10732996e-01,
          2.48278379e-02, -1.23438418e-01,  2.50698596e-01, -4.60321689e-03,
          2.35185307e-02, -2.72644132e-01,  3.34664196e-01, -4.34827171e-02,
         -2.80492604e-02, -3.24270219e-01, -2.32795000e-01,  2.65478253e-01,
          2.06407860e-01, -5.23197390e-02,  1.10645834e-02, -2.33840831e-02,
         -4.47062477e-02, -1

In [36]:
arr[0]

{'answer': 'ATACAND (candesartan cilexetil) is indicated for: \n\n•\tHypertension\no\tThe treatment of mild to moderate essential hypertension.\no\tATACAND may be used alone or concomitantly with thiazide diuretics.\no\tThe safety and efficacy of concurrent use with calcium channel blockers have not been established.\n•\tHeart Failure\no\tThe treatment of NYHA Class II and III heart failure with ejection fraction\n≤ 40% in addition to standard therapy, with or without an ACE inhibitor. ',
 'bert_vector': array([-2.12583378e-01, -9.25381780e-02, -7.74114877e-02,  2.08734050e-01,
         2.33869419e-01, -1.54881567e-01, -1.55370012e-01, -2.10732996e-01,
         2.48278379e-02, -1.23438418e-01,  2.50698596e-01, -4.60321689e-03,
         2.35185307e-02, -2.72644132e-01,  3.34664196e-01, -4.34827171e-02,
        -2.80492604e-02, -3.24270219e-01, -2.32795000e-01,  2.65478253e-01,
         2.06407860e-01, -5.23197390e-02,  1.10645834e-02, -2.33840831e-02,
        -4.47062477e-02, -1.6969586

In [37]:
for i in range(0,len(arr)):

    resp=es.index(index=IndexName,doc_type="_doc",id=i,body=arr[i])

In [38]:
resp

{'_index': 'bert_vec',
 '_type': '_doc',
 '_id': '98',
 '_version': 1,
 'result': 'created',
 '_shards': {'total': 1, 'successful': 1, 'failed': 0},
 '_seq_no': 98,
 '_primary_term': 1}

In [39]:
#testing
que = "what is ATACAND used for in america?"
que_vec=bc.encode([que])

In [40]:
que_vec

array([[ 1.85736373e-01, -2.07699046e-01, -1.89599261e-01,
         1.53252959e-01, -2.89510667e-01, -2.16531768e-01,
         4.33337897e-01,  2.95048267e-01,  2.28695229e-01,
         5.52341007e-02, -8.43904167e-02, -9.54468399e-02,
        -2.32339099e-01,  6.65739775e-02,  5.30490577e-01,
         1.54279947e-01, -4.03254032e-01, -3.43114167e-01,
         2.89174486e-02,  3.61027092e-01,  1.68039769e-01,
         3.93844575e-01, -1.60835788e-01,  8.84878449e-03,
         1.69550195e-01, -1.75638631e-01, -2.76611298e-01,
         2.11937889e-01,  1.01768181e-01, -1.49179608e-01,
         3.21527719e-01, -1.34792671e-01, -1.88379645e-01,
        -4.78655159e-01,  3.71874571e-01,  1.35099934e-02,
         2.90320963e-01, -8.23932067e-02, -1.08670844e-02,
         6.01970665e-02,  1.45278797e-01,  8.48062709e-02,
         8.41914639e-02, -2.22091407e-01, -4.62761447e-02,
         3.83935481e-01,  2.73067653e-01, -2.43884236e-01,
         9.83415917e-02, -7.83452243e-02,  2.62849987e-0

In [41]:
temp_prod=df["Product name"]
temp_country=df["country"]

In [44]:
set(temp_prod)

{'Candesartan cilexetil'}

In [45]:
set(temp_country)

{'Canada'}

In [48]:

script_query = {
"script_score": {
"query": {"term":{  
         "country":{  
            "value":"canada"
         }},
      "term":{"product":{
             "value":"candesartan cilexetil"   
            }}},
"script": {
"source": "Math.abs(cosineSimilarity(params.query_vector, doc['bert_vector']))",
"params": {"query_vector": que_vec[0] }
}}}

In [61]:
que_vec[0]

array([ 1.85736373e-01, -2.07699046e-01, -1.89599261e-01,  1.53252959e-01,
       -2.89510667e-01, -2.16531768e-01,  4.33337897e-01,  2.95048267e-01,
        2.28695229e-01,  5.52341007e-02, -8.43904167e-02, -9.54468399e-02,
       -2.32339099e-01,  6.65739775e-02,  5.30490577e-01,  1.54279947e-01,
       -4.03254032e-01, -3.43114167e-01,  2.89174486e-02,  3.61027092e-01,
        1.68039769e-01,  3.93844575e-01, -1.60835788e-01,  8.84878449e-03,
        1.69550195e-01, -1.75638631e-01, -2.76611298e-01,  2.11937889e-01,
        1.01768181e-01, -1.49179608e-01,  3.21527719e-01, -1.34792671e-01,
       -1.88379645e-01, -4.78655159e-01,  3.71874571e-01,  1.35099934e-02,
        2.90320963e-01, -8.23932067e-02, -1.08670844e-02,  6.01970665e-02,
        1.45278797e-01,  8.48062709e-02,  8.41914639e-02, -2.22091407e-01,
       -4.62761447e-02,  3.83935481e-01,  2.73067653e-01, -2.43884236e-01,
        9.83415917e-02, -7.83452243e-02,  2.62849987e-01, -6.21560495e-03,
       -2.66738296e-01, -

In [49]:
ans=es.search(index=IndexName,body={"size": 10,"query": script_query,"_source": {"includes": ["answer"]}})

/home/srinivas/anaconda3/envs/success/lib/python3.6/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: The vector functions of the form function(query, doc['field']) are deprecated, and the form function(query, 'field') should be used instead. For example, cosineSimilarity(query, doc['field']) is replaced by cosineSimilarity(query, 'field').
  warnings.warn(message, category=ElasticsearchDeprecationWarning)


In [50]:
ans

{'took': 19,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 99, 'relation': 'eq'},
  'max_score': 0.92611486,
  'hits': [{'_index': 'bert_vec',
    '_type': '_doc',
    '_id': '62',
    '_score': 0.92611486,
    '_source': {'answer': 'ATACAND may be taken with or without food '}},
   {'_index': 'bert_vec',
    '_type': '_doc',
    '_id': '17',
    '_score': 0.9217208,
    '_source': {'answer': 'There is limited experience regarding the administration of ATACAND in adult patients with renal transplant. '}},
   {'_index': 'bert_vec',
    '_type': '_doc',
    '_id': '30',
    '_score': 0.92167985,
    '_source': {'answer': 'Type 1 diabetes : There is no experience regarding the administration of ATACAND in children aged 6 to <17 years with type 1 diabetes. '}},
   {'_index': 'bert_vec',
    '_type': '_doc',
    '_id': '28',
    '_score': 0.9161656,
    '_source': {'answer': 'There is no experience regarding the admin

In [53]:
import re
def questions():
    count=0
    que_arr=[]
    for x in df["Possible Questions"]:
        sent=x.split("\n")
        for q in sent:
            if re.search('[a-zA-Z]',q)!=None:
                que_arr.append([q,count])
        count+=1
    return que_arr

In [54]:
que_arr=questions()

In [55]:
len(que_arr)

238

In [56]:
que_arr

[['What is ATACAND used for', 0],
 ['What is ATACAND used for in Canada', 0],
 ['How can ATACAND be used', 0],
 ['How can ATACAND be used in Canada', 0],
 ['Can ATACAND be used with calcium channel blockers', 0],
 ['Can ATACAND be used with calcium channel blockers in Canada', 0],
 ['Can ATACAND (candesartan cilexetil) be indicated for heartfailure', 0],
 ['What is the efficacy of ATACAND in elderly population', 1],
 ['What is the efficacy of ATACAND in elderly population in Canada', 1],
 ['What is the efficacy of ATACAND in Geriatrics (> 65 years of age) ', 1],
 ['What is ATACAND used for in children', 2],
 ['What is ATACAND used for in children in canada', 2],
 ['Can ATACAND be used to treat heart failure in children', 2],
 ['Can ATACAND be used to treat heart failure in children in canada', 2],
 ['Who is ATACAND conracindicated in', 3],
 ['Who is ATACAND conracindicated in canada', 3],
 ['What are the contraindications of ATACAND ind canada', 3],
 ['Can ATACAND be co-administered wi

In [57]:

def rank(ans):
    required=ans['hits']
    main_arr=required["hits"]
    count=1
    ids__=dict()
    for x in main_arr:
        id_no= x["_id"]

        score=x["_score"]

        answer_=x["_source"]["answer"]

        ids__[id_no.strip()]=1/count
        count+=1
    return ids__
    

In [58]:
ranker=rank(ans)

In [59]:
ranker

{'62': 1.0,
 '17': 0.5,
 '30': 0.3333333333333333,
 '28': 0.25,
 '15': 0.2,
 '33': 0.16666666666666666,
 '27': 0.14285714285714285,
 '63': 0.125,
 '8': 0.1111111111111111,
 '82': 0.1}

In [60]:
ans=es.search(index=IndexName,body={"size": 10,"query": script_query,"_source": {"includes": ["answer"]}})

In [62]:
total=0
count=0
recall_count=0
for x in que_arr:
    question=x[0].strip()
    print(question)
    id_number=str(x[1])
    que_vec=bc.encode([question])
    #print(que_vec)
    script_query = {
    "script_score": {
    "query": {"term":{  
             "country":{  
                "value":"canada"
             }},
          "term":{"product":{
                 "value":"candesartan cilexetil"   
                }}},
    "script": {
    "source": "Math.abs(cosineSimilarity(params.query_vector, doc['bert_vector']))",
    "params": {"query_vector": que_vec[0] }
    }}}
    ans=es.search(index=IndexName,body={"size": 10,"query": script_query,"_source": {"includes": ["answer"]}})
    ranker=rank(ans)
    if id_number in ranker:
        total+=ranker[id_number]
        print(ranker[id_number])
        recall_count+=1
    else:
        print(0)
    count+=1

print("mrr is"+str(total/count))
print("recall is"+str(recall_count/count))

What is ATACAND used for
[[ 1.45115286e-01 -2.80371666e-01 -2.28417981e-02  1.65393665e-01
  -1.51537433e-01 -3.58032644e-01  2.68135130e-01  1.80958197e-01
   2.17200503e-01 -3.41562659e-01 -5.70310615e-02  5.52905463e-02
  -2.52702199e-02  1.37814820e-01  3.59348267e-01  2.25741252e-01
  -7.53379911e-02 -1.87217087e-01 -2.57406175e-01 -1.64188072e-02
   2.95139253e-02 -4.58472315e-03  2.12219637e-02 -3.39915380e-02
   1.20898962e-01  7.14568049e-02 -2.30894014e-01 -4.68777828e-02
   8.60508829e-02  3.12346578e-01  8.64738524e-02  3.31348300e-01
   2.89805196e-02 -5.32642007e-01  2.31395274e-01 -8.36484805e-02
   1.41694188e-01 -4.12427396e-01 -2.50803500e-01 -1.32604912e-01
  -5.99490218e-02  9.44228694e-02  7.43871629e-02 -1.98596776e-01
  -9.72226858e-02  6.76545739e-01  6.54319823e-02 -5.34319691e-02
   2.64588982e-01  7.34646292e-03  3.24711680e-01 -1.72186196e-01
  -3.41630757e-01 -3.19948792e-01 -1.14609107e-01 -3.07955276e-02
  -2.02884987e-01 -4.49522771e-02  3.36718224e-02  

[[ 1.14201158e-01 -1.70892775e-01 -2.06750557e-01  1.70816973e-01
  -1.34461105e-01 -4.78619218e-01  2.01958492e-01  1.14538006e-01
   2.85572201e-01 -3.88082653e-01 -9.53985676e-02  5.53777516e-02
  -2.00448990e-01  7.82414079e-02  3.93705934e-01  1.61598966e-01
  -3.26075315e-01 -3.33408087e-01 -4.66825813e-03  1.49977669e-01
  -1.65720994e-03  4.22023050e-02 -1.84277669e-02 -3.98302525e-02
   1.29700199e-01 -6.41456619e-02 -1.75143555e-01  1.62539378e-01
   9.63752270e-02  1.21847697e-01 -1.42984174e-03  1.22491620e-01
   1.11315049e-01 -4.26438093e-01  1.37207523e-01 -1.78001001e-02
   2.58464336e-01 -1.99482858e-01 -2.54903257e-01  2.44995560e-02
   9.33895707e-02 -5.61160408e-02  1.59697413e-01 -2.03598738e-01
  -2.14500830e-01  4.22682047e-01 -8.48280787e-02 -4.11675461e-02
  -1.88553464e-02  1.34555086e-01  2.32564926e-01 -3.29791814e-01
  -5.07849216e-01 -4.03013855e-01 -3.45366374e-02 -2.33519435e-01
  -2.12295637e-01 -2.03477442e-01 -1.06268190e-01  2.39721194e-01
   4.86449

[[ 2.56315798e-01  1.02954451e-02  4.32891399e-02  1.10137194e-01
  -1.14621624e-01 -4.60287094e-01  2.16454357e-01  3.90876941e-02
   3.74921650e-01 -3.49697024e-01  1.53471753e-01  3.39860432e-02
   1.60656989e-01 -1.06891513e-01  2.87273914e-01  1.45042703e-01
  -5.16651124e-02 -1.63622692e-01 -1.52369529e-01 -6.70309961e-02
   1.33427158e-01  3.14093202e-01  6.36372566e-02 -1.37488902e-01
   2.47646302e-01 -6.54741526e-02  3.13195810e-02 -2.11299598e-01
  -7.12135956e-02  5.04279770e-02  2.02732667e-01  8.75272378e-02
  -7.43241534e-02 -4.33918625e-01  1.28382623e-01 -4.69332561e-02
   2.20266834e-01 -2.79046208e-01 -2.17298135e-01 -1.87541604e-01
  -3.52167040e-02  3.70263029e-03  4.23215181e-02 -2.37649888e-01
  -7.06313783e-03  3.20607603e-01  8.67989361e-02  2.24290658e-02
   1.91610470e-01 -4.70634364e-02  4.99769956e-01 -9.35562700e-02
  -3.36414456e-01 -5.02617121e-01 -1.32148072e-01 -1.38116069e-02
  -4.59805131e-02  9.87245962e-02  1.34294527e-02  2.39918232e-01
   7.33785

[[ 2.92971462e-01 -8.51524100e-02 -1.66969597e-01  5.97966760e-02
  -2.49381840e-01 -5.76976895e-01  1.84648812e-01  1.78647414e-01
   3.23643327e-01 -3.42849016e-01  1.04937963e-01 -6.36652559e-02
   1.25523955e-02 -1.42422915e-01  2.31832549e-01  2.14664593e-01
  -1.63098752e-01 -2.67726153e-01  3.76246194e-03 -9.66651365e-02
   4.32220213e-02  3.34467053e-01 -9.95221362e-03 -1.04783261e-02
   1.57506242e-01 -9.97772217e-02  7.23413154e-02  1.08202197e-01
  -6.56193197e-02 -1.02447709e-02  1.84154406e-01 -2.76410952e-02
   6.39480129e-02 -4.17127699e-01  2.07004964e-01  2.06143968e-02
   3.01770180e-01 -1.86563551e-01 -2.13728443e-01 -6.94321170e-02
  -6.85691014e-02 -1.39205530e-02 -8.51421878e-02 -3.36737603e-01
  -1.33686051e-01  2.73651779e-01 -9.02389511e-05  2.45565623e-02
   1.84924319e-01 -4.60868627e-02  4.31666613e-01 -1.89258590e-01
  -4.23157901e-01 -5.60244620e-01  2.96341050e-02 -1.35040477e-01
  -2.67396837e-01 -1.05744891e-01 -8.89216661e-02  2.85467565e-01
   2.04956

[[-5.20826206e-02 -7.29373768e-02 -3.00652571e-02  2.88403690e-01
   2.20937759e-01 -2.23491728e-01 -7.76896551e-02  1.14851967e-01
  -2.65452843e-02 -5.50776944e-02 -1.24537587e-01 -1.52137145e-01
  -1.74056999e-02  2.86408305e-01  3.90394241e-01  2.67753191e-02
  -8.14421326e-02 -1.37078479e-01 -3.54883641e-01 -1.61335468e-01
   2.25314885e-01  9.19424370e-02  5.07516116e-02  3.11341006e-02
   1.74722686e-01 -2.35284969e-01  5.70461564e-02 -1.46250859e-01
  -6.29443899e-02  8.57011601e-02  9.00661573e-02  1.44004211e-01
   1.26113743e-01 -1.64549693e-01  9.67676267e-02  9.90207586e-03
   2.22219452e-01 -3.50375801e-01  7.92913837e-04 -2.44007960e-01
   2.48016700e-01 -1.73489019e-01 -1.25673875e-01 -2.40239456e-01
  -7.52735091e-03  5.79171218e-02  2.28775963e-02 -1.28126383e-01
  -2.04851449e-01 -2.48874612e-02  5.49371123e-01  9.50722751e-05
  -1.99849591e-01 -2.43782938e-01  4.64330502e-02 -2.87541628e-01
  -2.21750721e-01 -3.40938032e-01 -2.84857899e-01  2.62102723e-01
   3.18236

...

[[-7.61749968e-02 -9.48333815e-02 -6.73101768e-02  1.90215364e-01
  -3.28390479e-01 -2.77891427e-01 -1.38970967e-02  2.88540572e-01
  -4.11687158e-02 -9.85792577e-02  5.00213169e-03 -2.23269239e-01
  -2.21846234e-02 -3.22002321e-02  3.28512713e-02  4.29955907e-02
   5.60392886e-02 -2.85025150e-01  2.20385611e-01  1.92553461e-01
   1.74697742e-01 -1.78715095e-01 -1.79923385e-01  7.95932859e-02
  -5.09332530e-02  4.96185794e-02 -1.15913779e-01  4.12286669e-01
   1.96963981e-01 -1.59561142e-01 -8.21164772e-02 -1.03468865e-01
  -1.09221190e-02 -9.34140459e-02  1.86301574e-01  3.96948084e-02
   1.66451380e-01 -3.10796618e-01  3.98769200e-01 -4.29067872e-02
   3.48568320e-01 -1.71881601e-01 -2.69439965e-01 -7.71383941e-02
   6.63487986e-02 -2.66066551e-01  9.99756157e-02  2.25996584e-01
  -1.50798112e-02  1.69800930e-02  3.05526435e-01 -1.50381133e-01
  -3.79406273e-01 -4.29143518e-01 -1.51744187e-01 -2.89489061e-01
   1.40367448e-01  1.35846391e-01 -1.87711045e-01  1.63862318e-01
   5.30414

[[ 3.78673345e-01  1.42479977e-02  2.24505290e-01  4.03098902e-03
  -4.32058610e-02 -5.14099419e-01 -1.74779996e-01  9.63702127e-02
   2.29573566e-02 -3.11855972e-01  2.87137683e-02 -2.72537977e-01
   1.65407225e-01  6.04976676e-02  9.40152705e-02 -2.26498172e-01
   3.19033056e-01 -1.54184476e-01  6.63480386e-02  4.64428775e-02
   2.64824837e-01  1.37209985e-02  3.46914642e-02  5.71651570e-02
  -1.88084878e-02 -2.56330132e-01 -1.51128829e-01  6.51356280e-01
   3.98137093e-01 -2.82733649e-01  2.55314380e-01 -2.64583249e-02
  -3.20199907e-01  4.33688127e-02  2.68338829e-01  3.39694798e-01
   8.93515907e-03 -3.00387964e-02  2.44626477e-01  2.29418557e-02
   1.83515072e-01 -3.23368981e-02 -4.05991346e-01  3.13923471e-02
  -7.94711113e-02  3.83504592e-02  2.53444731e-01 -6.40435889e-02
  -1.55213252e-01 -1.03112623e-01  3.42875034e-01  1.96964070e-01
   5.34966104e-02 -4.31186676e-01 -2.04660982e-01 -3.69275481e-01
   2.76451427e-02  3.64669770e-01 -4.95382436e-02  1.51902631e-01
   1.34387

[[ 2.86099672e-01 -1.22101400e-02  5.82533609e-03 -5.73900454e-02
  -1.51631370e-01 -5.28404832e-01 -2.13802472e-01  2.24706769e-01
   2.20167660e-03 -2.52054155e-01  6.95765624e-03 -1.39317140e-01
   2.02828959e-01  4.75707166e-02  1.09324120e-01 -1.21551424e-01
   2.36696735e-01 -1.85655162e-01  1.01084515e-01  5.59943169e-02
   3.13953519e-01  5.37983477e-02 -5.01085296e-02  1.74574673e-01
   7.71287456e-02 -2.10680604e-01 -8.69322717e-02  7.18102276e-01
   3.11042070e-01 -2.40259871e-01  1.90531537e-01 -1.48613364e-01
  -1.96071699e-01  4.93833385e-02  2.94940919e-01  2.93153286e-01
   2.23396868e-02 -9.39677507e-02  3.63830417e-01  6.98872283e-02
   1.57684490e-01 -3.80816609e-02 -3.75437707e-01 -8.75178259e-03
  -1.19808882e-01 -4.32182215e-02  2.67047852e-01  7.72083625e-02
  -1.30698085e-01 -2.06369348e-02  3.08785081e-01  6.91789314e-02
  -9.23502892e-02 -3.41501057e-01 -2.56583780e-01 -4.47266608e-01
  -8.11469462e-03  3.20300758e-01 -8.23800862e-02  8.77255946e-02
   2.74791

[[ 1.31730601e-01 -7.09185973e-02  2.45212074e-02  6.09692894e-02
  -1.23292752e-01 -5.16774118e-01 -1.22598968e-01  6.51285052e-02
  -6.80425391e-02 -2.49667287e-01 -1.60238400e-01 -3.94022018e-01
   1.83435991e-01  4.39450055e-01  1.65377125e-01 -1.29449382e-01
   3.30807000e-01 -2.25235596e-01  3.39980423e-03  2.34680086e-01
   1.91531107e-01  3.48979026e-01 -2.33211875e-01 -1.88725702e-02
   2.19700694e-01 -2.08144128e-01 -3.34831417e-01  5.36757708e-01
   2.59606361e-01 -1.30931795e-01  8.91734362e-02  1.50421038e-01
  -2.24651054e-01 -1.18258730e-01  5.00606716e-01  2.89801121e-01
   1.61700830e-01 -6.21361323e-02  1.59459293e-01 -9.57296863e-02
   1.99061528e-01 -9.97800678e-02 -2.44758919e-01  5.51335886e-02
   4.50178795e-02  2.38912385e-02 -1.96845517e-01 -3.69798578e-02
  -3.48155856e-01 -1.70823261e-01  1.21581666e-01  7.01497793e-02
  -1.94807611e-02 -7.78383493e-01 -1.52227521e-01 -3.54837865e-01
   3.30285847e-01  1.50249064e-01 -1.64171800e-01  1.70046180e-01
   2.85906

[[ 1.92316454e-02 -1.35536715e-01 -5.74912839e-02  1.39946431e-01
  -2.37201408e-01 -5.24205029e-01 -1.29949406e-01 -1.66034214e-02
  -1.85387626e-01 -3.05194557e-01 -1.38756424e-01 -3.43114465e-01
   8.98819566e-02  4.17845011e-01 -7.07365340e-03  1.32546555e-02
   3.34304512e-01 -2.67717510e-01  4.49842736e-02  3.16340268e-01
   6.71680123e-02  3.49770278e-01 -2.66653389e-01 -1.24838427e-01
   1.50652707e-01 -2.32198313e-01 -3.44982564e-01  5.61105728e-01
   2.27009609e-01 -1.77186266e-01  5.09125702e-02  8.77412793e-04
  -1.97609320e-01 -1.15814403e-01  5.56724787e-01  2.98939735e-01
   1.63391814e-01  2.31494397e-01  1.37457520e-01 -1.17597662e-01
   4.77014109e-02 -9.63785965e-03 -3.92383635e-01  9.78208333e-02
  -2.22780854e-02 -1.17339134e-01 -1.45181445e-02  2.62509249e-02
  -3.41706663e-01 -2.87497900e-02  4.93826680e-02  1.32229760e-01
  -7.64867365e-02 -6.02572381e-01 -1.37553722e-01 -2.63442099e-01
   1.93320036e-01  5.34404889e-02  9.65489820e-03  1.91029608e-01
   1.23328